# 成年人死亡率预测

<br>
<hr>

## 1. 实验介绍

### 1.1 实验背景

成年人死亡率指的是每一千人中15岁至60岁死亡的概率（数学期望）。这里我们给出了世界卫生组织（WHO）下属的全球卫生观察站（GHO）数据存储库跟踪的所有国家健康状况以及许多其他相关因素。要求利用训练数据建立回归模型，并预测成年人死亡率（**Adult Mortality**）。

### 1.2 实验要求

1. 训练数据包含`2336`条记录和`22`个字段，对训练数据进行一定的可视化数据分析（章节2.2）
2. 利用训练数据，选择合适的信息作为特征建立回归模型，并预测测试数据成年人死亡率
3. 利用`MO`平台进行模型性能评估

### 1.3 实验环境
可以使用基于 Python 的 `Pandas` 库进行数据相关处理，使用 `Sklearn` 库进行相关模型构建。


### 1.4 注意事项
1. 推荐使用基于 Python 的`Sklearn`库进行相关实验
2. 数据中可能会有一些字段的值存在缺失

## 2. 实验部分

### 2.1 导入相关包

In [7]:
from pathlib import Path

import pandas as pd
import sklearn
import numpy as np

from sklearn.impute import SimpleImputer
from sklearn.preprocessing import MinMaxScaler
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, r2_score

import joblib


### 2.2 数据读取和可视化分析

In [18]:
# 读取数据集
train_data = pd.read_csv('./data/train_data.csv')
train_data.rename(columns={k:k.replace('  ', ' ').strip() for k in train_data.columns}, inplace=True)


In [ ]:
from pathlib import Path

import pandas as pd

desc_res_folder = Path('results')
desc_res_folder.mkdir(exist_ok=True, parents=True)

catecorical_features = ['Country', 'Status']
numeric_features = list(set(train_data.columns) - set(catecorical_features))

feat_info = {
    "Country": "国家",
    "Year": "年份",
    "Status": "发达国家或发展中国家",
    "Life expectancy": "预期寿命",
    "Infant deaths": "每千人口中的婴儿死亡人数",
    "Alcohol": "人均酒精消费量（以升纯酒精为单位）",
    "percentage expenditure": "卫生支出占人均国内生产总值的百分比",
    "Hepatitis B": "一岁儿童乙型肝炎免疫疫苗接种率",
    "Measles": "麻疹每1000人报告的病例数",
    "BMI": "所有人群平均BMI指数",
    "under-five deaths": "每千人口中五岁以下死亡人数",
    "Polio": "1岁儿童脊髓灰质炎免疫覆盖率（%）",
    "Total expenditure": "政府卫生支出占政府总支出的百分比",
    "Diphtheria": "1岁儿童白喉、破伤风类毒素和百日咳免疫接种率（%）",
    "HIV/AIDS": "每千名活产婴儿死于艾滋病毒/艾滋病（0-4岁）",
    "GDP": "人均国内生产总值（美元）",
    "Population": "人口",
    "thinness 1-19 years": "10至19岁儿童和青少年的消瘦流行率",
    "thinness 5-9 years": "5至9岁儿童中的消瘦流行率",
    "Income composition of resources": "财力收入构成方面的人类发展指数（从0到1）",
    "Schooling": "受教育年限",
    "Adult Mortality": "成人死亡率（每1000人中15至60岁死亡的概率）",
}

description = train_data[catecorical_features].describe()
feat_info_df = pd.DataFrame([{k: v for k, v in feat_info.items() if k in description.columns}],index = ['简介'])
description = pd.concat([feat_info_df,description], axis=0)
description.to_csv(desc_res_folder / 'train_data_description catecorical.csv')

description = train_data[numeric_features].describe()
feat_info_df = pd.DataFrame([{k: v for k, v in feat_info.items() if k in description.columns}],index = ['简介'])
description = pd.concat([feat_info_df,description], axis=0)
description.to_csv(desc_res_folder / 'train_data_description numeric.csv')

                                  count          mean           std  \
Year                             2336.0  2.007500e+03  4.610759e+00   
Life expectancy                  2336.0  6.915274e+01  9.615927e+00   
infant deaths                    2336.0  3.056079e+01  1.163212e+02   
Alcohol                          2180.0  4.610491e+00  4.069272e+00   
percentage expenditure           2336.0  7.603620e+02  2.026541e+03   
Hepatitis B                      1877.0  8.120884e+01  2.473523e+01   
Measles                          2336.0  2.526246e+03  1.210219e+04   
 BMI                             2309.0  3.805284e+01  2.002013e+01   
under-five deaths                2336.0  4.251156e+01  1.589374e+02   
Polio                            2319.0  8.247348e+01  2.354716e+01   
Total expenditure                2151.0  5.936555e+00  2.504335e+00   
Diphtheria                       2319.0  8.235188e+01  2.380367e+01   
 HIV/AIDS                        2336.0  1.764598e+00  5.021892e+00   
GDP   

可以看到训练数据包含2336条记录和22个字段，每个字段含义说明如下：
1. Country：国家
2. Year：年份
3. Status：发达国家或发展中国家
4. Life expectancy：预期寿命
5. Infant deaths：每千人口中的婴儿死亡人数
6. Alcohol：人均酒精消费量（以升纯酒精为单位）
7. percentage expenditure：卫生支出占人均国内生产总值的百分比
8. Hepatitis B：一岁儿童乙型肝炎免疫疫苗接种率
9. Measles：麻疹每1000人报告的病例数
10. BMI：所有人群平均BMI指数
11. under-five deaths：每千人口中五岁以下死亡人数
12. Polio：1岁儿童脊髓灰质炎免疫覆盖率（%）
13. Total expenditure：政府卫生支出占政府总支出的百分比
14. Diphtheria：1岁儿童白喉、破伤风类毒素和百日咳免疫接种率（%）
15. HIV/AIDS：每千名活产婴儿死于艾滋病毒/艾滋病（0-4岁）
16. GDP：人均国内生产总值（美元）
17. Population：人口
18. thinness 1-19 years：10至19岁儿童和青少年的消瘦流行率
19. thinness 5-9 years：5至9岁儿童中的消瘦流行率
20. Income composition of resources：财力收入构成方面的人类发展指数（从0到1）
21. Schooling：受教育年限
22. Adult Mortality：成人死亡率（每1000人中15至60岁死亡的概率）

其中`Adult Mortality`字段为要预测的标签(`label`)

In [ ]:
# 查看数据集大小
train_data.shape


In [4]:
# 计算各个特征之间的皮尔森相关系数
column_name = ['Year', 'Life expectancy ', 'infant deaths', 'Alcohol',
           'percentage expenditure', 'Hepatitis B', 'Measles ', ' BMI ', 'under-five deaths ',
           'Polio', 'Total expenditure', 'Diphtheria ', ' HIV/AIDS', 'GDP', 'Population',
           ' thinness  1-19 years', ' thinness 5-9 years', 'Income composition of resources',
           'Schooling']
train_data[column_name].corr()

Year  Life expectancy   infant deaths  \
Year                             1.000000          0.173044      -0.045574   
Life expectancy                  0.173044          1.000000      -0.200307   
infant deaths                   -0.045574         -0.200307       1.000000   
Alcohol                         -0.059393          0.403930      -0.117509   
percentage expenditure           0.027351          0.385335      -0.088942   
Hepatitis B                      0.119861          0.250026      -0.233426   
Measles                         -0.089535         -0.156621       0.502258   
 BMI                             0.097642          0.563239      -0.227356   
under-five deaths               -0.051892         -0.227572       0.996460   
Polio                            0.099639          0.470405      -0.168905   
Total expenditure                0.095594          0.227194      -0.127455   
Diphtheria                       0.146898          0.500060      -0.186393   
 HIV/AIDS                       -0.144159         -0.558550       0.027106   
GDP                              0.094351          0.466012      -0.112767   
Population                       0.012174         -0.028874       0.559472   
 thinness  1-19 years           -0.049637         -0.481919       0.462870   
 thinness 5-9 years             -0.055414         -0.476773       0.466544   
Income composition of resources  0.244558          0.720200      -0.148067   
Schooling                        0.219591          0.756970      -0.197907   

                                  Alcohol  percentage expenditure  \
Year                            -0.059393                0.027351   
Life expectancy                  0.403930                0.385335   
infant deaths                   -0.117509               -0.088942   
Alcohol                          1.000000                0.351033   
percentage expenditure           0.351033                1.000000   
Hepatitis B                      0.076217                0.020959   
Measles                         -0.045272               -0.056564   
 BMI                             0.328996                0.243372   
under-five deaths               -0.114326               -0.091140   
Polio                            0.223054                0.153229   
Total expenditure                0.297324                0.196985   
Diphtheria                       0.225653                0.149584   
 HIV/AIDS                       -0.053149               -0.102281   
GDP                              0.367267                0.908855   
Population                      -0.032890               -0.030910   
 thinness  1-19 years           -0.437330               -0.257604   
 thinness 5-9 years             -0.425520               -0.258956   
Income composition of resources  0.451557                0.386001   
Schooling                        0.545457                0.399577   

                                 Hepatitis B  Measles       BMI   \
Year                                0.119861 -0.089535  0.097642   
Life expectancy                     0.250026 -0.156621  0.563239   
infant deaths                      -0.233426  0.502258 -0.227356   
Alcohol                             0.076217 -0.045272  0.328996   
percentage expenditure              0.020959 -0.056564  0.243372   
Hepatitis B                         1.000000 -0.122937  0.166267   
Measles                            -0.122937  1.000000 -0.176633   
 BMI                                0.166267 -0.176633  1.000000   
under-five deaths                  -0.243389  0.510569 -0.237654   
Polio                               0.470815 -0.143172  0.287353   
Total expenditure                   0.054130 -0.106506  0.231999   
Diphtheria                          0.610947 -0.151227  0.304195   
 HIV/AIDS                          -0.112097  0.033809 -0.243694   
GDP                                 0.084776 -0.078137  0.318139   
Population                         -0.125556  0.248298 -0.074910   
 thinne

In [5]:
# 将相关性矩阵绘制成热力图
corr = train_data[column_name].corr()
corr.style.background_gradient(cmap='coolwarm')


Duplicate key in file PosixPath('/usr/local/lib/python3.9/dist-packages/matplotlib/mpl-data/matplotlibrc'), line 801 ('font.family: sans-serif')
Duplicate key in file PosixPath('/usr/local/lib/python3.9/dist-packages/matplotlib/mpl-data/matplotlibrc'), line 802 ('font.sans-serif: SimHei')


In [6]:
# 利用seaborn检查可视化数据之间的依赖关系
import seaborn as sns
sns.pairplot(train_data[column_name])

### 2.3 模型拟合和成年人死亡率预测

要求同学们利用训练数据来建立回归模型，我们已经给出了一个可运行的基础代码，同学们可以对此进行参考

In [7]:
train_data = pd.read_csv('./data/train_data.csv')
model_filename = './model.pkl'
imputer_filename = './imputer.pkl'
scaler_filename = './scaler.pkl'


In [8]:
def preprocess_data(data, imputer=None, scaler=None):

    column_name = ['Year', 'Life expectancy ', 'infant deaths', 'Alcohol',
               'percentage expenditure', 'Hepatitis B', 'Measles ', ' BMI ', 'under-five deaths ',
               'Polio', 'Total expenditure', 'Diphtheria ', ' HIV/AIDS', 'GDP', 'Population',
               ' thinness  1-19 years', ' thinness 5-9 years', 'Income composition of resources',
               'Schooling']
    data = data.drop(["Country", "Status"], axis=1)

    if imputer==None:
        imputer = SimpleImputer(strategy='mean', missing_values=np.nan)
        imputer = imputer.fit(data[column_name])
    data[column_name] = imputer.transform(data[column_name])

    if scaler==None:
        scaler = MinMaxScaler()
        scaler = scaler.fit(data)
    data_norm = pd.DataFrame(scaler.transform(data), columns=data.columns)

    data_norm = data_norm.drop(['Year'], axis = 1)

    return data_norm, imputer, scaler


In [ ]:
def model_fit(train_data):

    train_y = train_data.iloc[:,-1].values
    train_data = train_data.drop(["Adult Mortality"], axis=1)
    train_data_norm, imputer, scaler = preprocess_data(train_data)

    train_x = train_data_norm.values

    regressor = LinearRegression()
    regressor.fit(train_x, train_y)

    joblib.dump(regressor, model_filename)
    joblib.dump(imputer, imputer_filename)
    joblib.dump(scaler, scaler_filename)

    return regressor


In [ ]:
def predict(test_data, filename):
    loaded_model = joblib.load(model_filename)
    imputer = joblib.load(imputer_filename)
    scaler = joblib.load(scaler_filename)

    test_data_norm, _, _ = preprocess_data(test_data, imputer, scaler)
    test_x = test_data_norm.values
    predictions = loaded_model.predict(test_x)

    return predictions


In [ ]:
model = model_fit(train_data)


In [ ]:
# 打印模型的截距
print(model.intercept_)


In [ ]:
# 打印模型的斜率
print(model.coef_)


### 2.4 模型性能评估

我们可以看一下模型在训练集上的表现：

In [ ]:
label = train_data.loc[:,'Adult Mortality']
data = train_data.iloc[:,:-1]
y_pred = predict(data, './model.pkl')
r2 = r2_score(label, y_pred)
mse = mean_squared_error(label, y_pred)
print("MSE is {}".format(mse))
print("R2 score is {}".format(r2))


## 3. 作业提交

**作业要求及注意事项**：    
             
1. 点击左侧栏提交作业后点击【生成文件】则需要勾选与预测 predict() 函数的 cell相关的其它cell ，并将其转化成为 main.py 文件。                       
2. 请导入必要的包和第三方库以及该模型所依赖的 py 文件 (包括此文件中曾经导入过的)。             
3. 请加载你认为训练最佳的模型，即请按要求填写模型路径。              
4. `predict()` 函数的输入输出及函数名称请不要改动。
5. 提交的作业包括【程序报告.pdf】和对应的ipynb文件

===========================================  **模型预测代码答题区域**  ===========================================  
在下方的代码块中编写 **模型预测** 部分的代码，请勿在别的位置作答

In [ ]:
import pandas as pd
import sklearn
import numpy as np

from sklearn.impute import SimpleImputer
from sklearn.preprocessing import MinMaxScaler
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, r2_score

import joblib

model_filename = './model.pkl'
imputer_filename = './imputer.pkl'
scaler_filename = './scaler.pkl'

def preprocess_data(data, imputer=None, scaler=None):

# -------------------------- 请调整你的数据预处理过程 ---------------------------
## 输入：
#### data 为 pandas.DataFrame类型数据
#### imputer 为缺失值填充方式
#### scaler 为数据归一化方式
## 输出：
#### data_norm 为处理后的数据，为 pandas.DataFrame类型数据

    column_name = ['Year', 'Life expectancy ', 'infant deaths', 'Alcohol',
               'percentage expenditure', 'Hepatitis B', 'Measles ', ' BMI ', 'under-five deaths ',
               'Polio', 'Total expenditure', 'Diphtheria ', ' HIV/AIDS', 'GDP', 'Population',
               ' thinness  1-19 years', ' thinness 5-9 years', 'Income composition of resources',
               'Schooling']
    data = data.drop(["Country", "Status"], axis=1)

    if imputer==None:
        imputer = SimpleImputer(strategy='mean', missing_values=np.nan)
        imputer = imputer.fit(data[column_name])
    data[column_name] = imputer.transform(data[column_name])

    if scaler==None:
        scaler = MinMaxScaler()
        scaler = scaler.fit(data)
    data_norm = pd.DataFrame(scaler.transform(data), columns=data.columns)

    data_norm = data_norm.drop(['Year'], axis = 1)

    return data_norm

def predict(test_data):

# -------------------------- 请加载您最满意的模型 ---------------------------
# 加载模型(请加载你认为的最佳模型)
# 加载模型,加载请注意 filename 是相对路径, 与当前文件同级。
# test_data 为 pandas.DataFrame类型数据
    loaded_model = joblib.load(model_filename)
    imputer = joblib.load(imputer_filename)
    scaler = joblib.load(scaler_filename)

    test_data_norm = preprocess_data(test_data, imputer, scaler)
    test_x = test_data_norm.values
    predictions = loaded_model.predict(test_x)

    return predictions


In [2]:
import sys
import time

import matplotlib.pyplot as plt
# 导入相关包
import pandas as pd
import sklearn
import numpy as np

from sklearn.impute import SimpleImputer
from sklearn import preprocessing
import sklearn.linear_model as lm
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error, r2_score

import joblib
import seaborn as sns
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV

# 数据读取和可视化分析
model_filename = './best_model/model.pkl'
imputer_filename = './best_model/imputer.pkl'
scaler_filename = './best_model/scaler.pkl'

train_data = pd.read_csv('./data/train_data.csv')


def preprocess_data(data, imputer=None, scaler=None):
    column_name = ['Year', 'Life expectancy ', 'infant deaths', 'Alcohol',
                   'percentage expenditure', 'Hepatitis B', 'Measles ', ' BMI ', 'under-five deaths ',
                   'Polio', 'Total expenditure', 'Diphtheria ', ' HIV/AIDS', 'GDP', 'Population',
                   ' thinness  1-19 years', ' thinness 5-9 years', 'Income composition of resources',
                   'Schooling']
    data = data.drop(["Country", "Status"], axis=1)

    if imputer == None:
        imputer = SimpleImputer(strategy='mean', missing_values=np.nan)
        imputer = imputer.fit(data[column_name])
    data[column_name] = imputer.transform(data[column_name])

    if scaler == None:
        scaler = preprocessing.MinMaxScaler()
        scaler = scaler.fit(data)
    data_norm = pd.DataFrame(scaler.transform(data), columns=data.columns)

    data_norm = data_norm.drop(['Year'], axis=1)

    return data_norm, imputer, scaler

def model_fit(train_data=None):
    train_y = train_data.iloc[:, -1].values
    train_data = train_data.drop(["Adult Mortality"], axis=1)
    x_data_norm, imputer, scaler = preprocess_data(train_data)

    train_x = x_data_norm.values

    # # 线性回归
    # regressor = lm.LinearRegression()
    # regressor.fit(train_x, train_y)

    # 随机森林回归
    regressor = RandomForestRegressor(bootstrap=True, oob_score=True, random_state=1,
                                      n_estimators=450, max_depth=8, max_features=18,
                                      max_samples=0.96, min_samples_leaf=1, min_samples_split=3)
    regressor.fit(train_x, train_y)

    joblib.dump(regressor, model_filename)
    joblib.dump(imputer, imputer_filename)
    joblib.dump(scaler, scaler_filename)

    return regressor

def predict(test_data):
    loaded_model = joblib.load(model_filename)
    imputer = joblib.load(imputer_filename)
    scaler = joblib.load(scaler_filename)

    test_data_norm, _, _ = preprocess_data(test_data, imputer, scaler)
    test_x = test_data_norm.values
    predictions = loaded_model.predict(test_x)

    return predictions

In [6]:
def model_fit(train_data=None):
    train_y = train_data.iloc[:, -1].values
    train_data = train_data.drop(["Adult Mortality"], axis=1)
    x_data_norm, imputer, scaler = preprocess_data(train_data)

    train_x = x_data_norm.values

    # # 线性回归
    # regressor = lm.LinearRegression()
    # regressor.fit(train_x, train_y)

    # 随机森林回归
    regressor = RandomForestRegressor(bootstrap=True, oob_score=True, random_state=1,
                                      n_estimators=170, max_depth=16, max_features=36,
                                      max_samples=0.96, min_samples_leaf=1, min_samples_split=3)
    regressor.fit(train_x, train_y)

    joblib.dump(regressor, model_filename)
    joblib.dump(imputer, imputer_filename)
    joblib.dump(scaler, scaler_filename)

    return regressor

if __name__ == '__main__':
    # DataVisualization()

    # # GridSearch寻找最优模型参数组
    # t1 = time.time()
    # best_model = gridsearch()
    # t2 = time.time()
    # print(f'GridSearch cost:{t2-t1} s')
    # print(f'Best params:{best_model.best_params_}')
    # print(f'Best score:{best_model.best_score_}')

    # 使用最优参数组训练模型
    model = model_fit(train_data)
    # # 打印模型的截距
    # print(f'Model_intercept:{model.intercept_}')
    # # 打印模型的斜率
    # print(f'Model_coef:{model.coef_}')

    # 模型性能评估
    label = train_data.loc[:, 'Adult Mortality']
    data = train_data.iloc[:, :-1]
    # label = y_test
    # data = x_test
    y_pred = predict(data)
    r2 = r2_score(label, y_pred)
    mse = mean_squared_error(label, y_pred)
    print("MSE is {}".format(mse))
    print("R2 score is {}".format(r2))

MSE is 1075.6585880768137
R2 score is 0.9308111498901857
